In [51]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from time import sleep
import random
import os

# Verify the ChromeDriver path
chrome_driver_path = "D:\\Downloads\\chromedriver-win64\\chromedriver-win64\\chromedriver.exe"
if not os.path.exists(chrome_driver_path):
    raise FileNotFoundError(f"ChromeDriver not found at {chrome_driver_path}")

# Set up the ChromeDriver service
service = Service(executable_path=chrome_driver_path)

# Setting up ChromeDriver with anti-detection measures
options = webdriver.ChromeOptions()
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)

# Initialize the WebDriver with the Service object
try:
    driver = webdriver.Chrome(service=service, options=options)
except Exception as e:
    print(f"Failed to initialize WebDriver: {e}")
    raise

# Adding anti-detection measures
driver.execute_cdp_cmd("Page.addScriptToEvaluateOnNewDocument", {
    "source": "Object.defineProperty(navigator, 'webdriver', {get: () => undefined})"
})

# Sofascore Singapore Premier League URL
base_url = "https://www.sofascore.com/tournament/football/singapore/premier-league/634#id:59708"

def scrape_singaporean_players():
    driver.get(base_url)
    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

    # Navigate to each team page
    teams = driver.find_elements(By.CSS_SELECTOR, "a[href*='/team/']")
    for team in teams:
        team_name = team.text
        team_url = team.get_attribute('href')
        print(f"Scraping team: {team_name}")
        
        driver.get(team_url)
        sleep(random.uniform(1, 3))  # Random delay to mimic human interaction

        players = driver.find_elements(By.CSS_SELECTOR, "a[href*='/player/']")
        for player in players:
            player_name = player.text
            player_url = player.get_attribute('href')

            # Navigate to player page
            driver.get(player_url)
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

            # Example: check for Singapore nationality (update selector as necessary)
            try:
                nationality = driver.find_element(By.XPATH, "//div[contains(text(),'Singapore')]")
                if nationality:
                    print(f"Singaporean player found: {player_name}, URL: {player_url}")
                    # Extract player stats here, using the correct HTML structure
                    # (e.g., appearances, goals, assists, etc.)
                    # Save or process the data as needed
                    
            except Exception as e:
                print(f"Player {player_name} does not match criteria or an error occurred: {e}")

            driver.back()
            sleep(random.uniform(1, 3))  # Random delay after each player

    # Close the driver after scraping
    driver.quit()

scrape_singaporean_players()


Scraping team: 1
Tampines Rovers
12
+26
30


StaleElementReferenceException: Message: stale element reference: stale element not found
  (Session info: chrome=127.0.6533.120); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#stale-element-reference-exception
Stacktrace:
	GetHandleVerifier [0x00007FF6C4F89632+30946]
	(No symbol) [0x00007FF6C4F3E3C9]
	(No symbol) [0x00007FF6C4E36FDA]
	(No symbol) [0x00007FF6C4E4963D]
	(No symbol) [0x00007FF6C4E4A09A]
	(No symbol) [0x00007FF6C4E3E73B]
	(No symbol) [0x00007FF6C4E3C506]
	(No symbol) [0x00007FF6C4E3FD31]
	(No symbol) [0x00007FF6C4E3FDD0]
	(No symbol) [0x00007FF6C4E8226B]
	(No symbol) [0x00007FF6C4EACA6A]
	(No symbol) [0x00007FF6C4E7BBB6]
	(No symbol) [0x00007FF6C4EACC80]
	(No symbol) [0x00007FF6C4ECB041]
	(No symbol) [0x00007FF6C4EAC813]
	(No symbol) [0x00007FF6C4E7A6E5]
	(No symbol) [0x00007FF6C4E7B021]
	GetHandleVerifier [0x00007FF6C50BF83D+1301229]
	GetHandleVerifier [0x00007FF6C50CBDB7+1351783]
	GetHandleVerifier

### Copilot

In [93]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException, TimeoutException
from time import sleep
import random
import os

# Verify the ChromeDriver path
chrome_driver_path = "D:\\Downloads\\chromedriver-win64\\chromedriver-win64\\chromedriver.exe"
if not os.path.exists(chrome_driver_path):
    raise FileNotFoundError(f"ChromeDriver not found at {chrome_driver_path}")

# Set up the ChromeDriver service
service = Service(executable_path=chrome_driver_path)

# Setting up ChromeDriver with anti-detection measures
options = webdriver.ChromeOptions()
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)

# Initialize the WebDriver with the Service object
try:
    driver = webdriver.Chrome(service=service, options=options)
except Exception as e:
    print(f"Failed to initialize WebDriver: {e}")
    raise

# Adding anti-detection measures
driver.execute_cdp_cmd("Page.addScriptToEvaluateOnNewDocument", {
    "source": "Object.defineProperty(navigator, 'webdriver', {get: () => undefined})"
})

# Sofascore Singapore Premier League URL
base_url = "https://www.sofascore.com/tournament/football/singapore/premier-league/634#id:59708"

def retrying_find_elements(driver, by, value, attempts=5):
    for attempt in range(attempts):
        try:
            elements = driver.find_elements(by, value)
            if elements:
                return elements
        except StaleElementReferenceException:
            if attempt < attempts - 1:
                sleep(1)
            else:
                raise
    return []

def scrape_singaporean_players():
    driver.get(base_url)
    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

    # Navigate to each team page
    teams = retrying_find_elements(driver, By.CSS_SELECTOR, "a[href*='/team/']")
    for i in range(len(teams)):
        attempts = 0
        while attempts < 5:
            try:
                if i >= len(teams):
                    print("Index out of range, breaking loop.")
                    break
                team = teams[i]
                team_name = team.text
                team_url = team.get_attribute('href')
                print(f"Scraping team: {team_name}")
                break
            except StaleElementReferenceException:
                attempts += 1
                teams = retrying_find_elements(driver, By.CSS_SELECTOR, "a[href*='/team/']")

        if attempts == 5:
            print(f"Failed to retrieve team {i}, skipping.")
            continue

        driver.get(team_url)
        sleep(random.uniform(1, 3))  # Random delay to mimic human interaction

        players = retrying_find_elements(driver, By.CSS_SELECTOR, "a[href*='/player/']")
        for player in players:
            player_name = player.text
            player_url = player.get_attribute('href')

            # Navigate to player page
            driver.get(player_url)
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

            # Example: check for Singapore nationality (update selector as necessary)
            try:
                nationality = driver.find_element(By.XPATH, "//div[contains(text(),'Singapore')]")
                if nationality:
                    print(f"Singaporean player found: {player_name}, URL: {player_url}")
                    # Extract player stats here, using the correct HTML structure
                    # (e.g., appearances, goals, assists, etc.)
                    # Save or process the data as needed
                    
            except Exception as e:
                print(f"Player {player_name} does not match criteria or an error occurred: {e}")

            driver.back()
            sleep(random.uniform(1, 3))  # Random delay after each player

    # Close the driver after scraping
    driver.quit()

scrape_singaporean_players()


Scraping team: 1
Tampines Rovers
12
+26
30
Index out of range, breaking loop.
Index out of range, breaking loop.
Index out of range, breaking loop.
Index out of range, breaking loop.
Index out of range, breaking loop.
Index out of range, breaking loop.
Index out of range, breaking loop.
Index out of range, breaking loop.


### Copilot 2 team scrape successfull

In [97]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException, TimeoutException
from time import sleep
import random
import os

# Verify the ChromeDriver path
chrome_driver_path = "D:\\Downloads\\chromedriver-win64\\chromedriver-win64\\chromedriver.exe"
if not os.path.exists(chrome_driver_path):
    raise FileNotFoundError(f"ChromeDriver not found at {chrome_driver_path}")

# Set up the ChromeDriver service
service = Service(executable_path=chrome_driver_path)

# Setting up ChromeDriver with anti-detection measures
options = webdriver.ChromeOptions()
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)

# Initialize the WebDriver with the Service object
try:
    driver = webdriver.Chrome(service=service, options=options)
except Exception as e:
    print(f"Failed to initialize WebDriver: {e}")
    raise

# Adding anti-detection measures
driver.execute_cdp_cmd("Page.addScriptToEvaluateOnNewDocument", {
    "source": "Object.defineProperty(navigator, 'webdriver', {get: () => undefined})"
})

# Sofascore Singapore Premier League URL
base_url = "https://www.sofascore.com/tournament/football/singapore/premier-league/634#id:59708"

def retrying_find_elements(driver, by, value, attempts=5):
    for attempt in range(attempts):
        try:
            elements = driver.find_elements(by, value)
            if elements:
                return elements
        except StaleElementReferenceException:
            if attempt < attempts - 1:
                sleep(1)
            else:
                raise
    return []

def scrape_singaporean_players():
    driver.get(base_url)
    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

    # Fetch the list of teams once
    teams = retrying_find_elements(driver, By.CSS_SELECTOR, "a[href*='/team/']")
    team_urls = [(team.text, team.get_attribute('href')) for team in teams]

    for team_name, team_url in team_urls:
        print(f"Scraping team: {team_name}")

        driver.get(team_url)
        sleep(random.uniform(1, 3))  # Random delay to mimic human interaction

        players = retrying_find_elements(driver, By.CSS_SELECTOR, "a[href*='/player/']")
        for player in players:
            player_name = player.text
            player_url = player.get_attribute('href')

            # Navigate to player page
            driver.get(player_url)
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

            # Example: check for Singapore nationality (update selector as necessary)
            try:
                nationality = driver.find_element(By.XPATH, "//div[contains(text(),'Singapore')]")
                if nationality:
                    print(f"Singaporean player found: {player_name}, URL: {player_url}")
                    # Extract player stats here, using the correct HTML structure
                    # (e.g., appearances, goals, assists, etc.)
                    # Save or process the data as needed
                    
            except Exception as e:
                print(f"Player {player_name} does not match criteria or an error occurred: {e}")

            driver.back()
            sleep(random.uniform(1, 3))  # Random delay after each player

    # Close the driver after scraping
    driver.quit()

scrape_singaporean_players()


Scraping team: 1
Tampines Rovers
12
+26
30
Scraping team: 2
Lion City Sailors
11
+28
28
Scraping team: 3
Geylang Int.
12
+20
21
Scraping team: 4
Balestier Khalsa
11
+2
16
Scraping team: 5
Hougang Utd
12
-12
13
Scraping team: 6
Albirex Niigata
12
-15
10
Scraping team: 7
Young Lions
12
-18
10
Scraping team: 8
DPMM
11
-9
9
Scraping team: 9
Tanjong Pagar Utd.
11
-22
7


### Player scrape

In [124]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException, TimeoutException, NoSuchElementException
from time import sleep
import random
import os

# Verify the ChromeDriver path
chrome_driver_path = "D:\\Downloads\\chromedriver-win64\\chromedriver-win64\\chromedriver.exe"
if not os.path.exists(chrome_driver_path):
    raise FileNotFoundError(f"ChromeDriver not found at {chrome_driver_path}")

# Set up the ChromeDriver service
service = Service(executable_path=chrome_driver_path)

# Setting up ChromeDriver with anti-detection measures
options = webdriver.ChromeOptions()
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)

# Initialize the WebDriver with the Service object
try:
    driver = webdriver.Chrome(service=service, options=options)
except Exception as e:
    print(f"Failed to initialize WebDriver: {e}")
    raise

# Adding anti-detection measures
driver.execute_cdp_cmd("Page.addScriptToEvaluateOnNewDocument", {
    "source": "Object.defineProperty(navigator, 'webdriver', {get: () => undefined})"
})

# List of team URLs
team_urls = [
    "https://www.sofascore.com/team/football/tampines-rovers/3043",
    "https://www.sofascore.com/team/football/lion-city-sailors/3041",
    "https://www.sofascore.com/team/football/geylang-international/3044",
    "https://www.sofascore.com/team/football/balestier-khalsa/3039",
    "https://www.sofascore.com/team/football/hougang-united/34083",
    "https://www.sofascore.com/team/football/albirex-niigata/34081",
    "https://www.sofascore.com/team/football/young-lions/34082",
    "https://www.sofascore.com/team/football/tanjong-pagar-united/3038"
]

def retrying_find_elements(driver, by, value, attempts=5):
    for attempt in range(attempts):
        try:
            elements = driver.find_elements(by, value)
            if elements:
                return elements
        except StaleElementReferenceException:
            if attempt < attempts - 1:
                sleep(1)
            else:
                raise
    return []

def scrape_player_stats():
    for team_url in team_urls:
        driver.get(team_url)
        WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))
        sleep(random.uniform(1, 3))  # Random delay to mimic human interaction

        # Debugging: Print the page source to verify if player elements are present
        print(f"Page source for team URL: {team_url}")
        print(driver.page_source)

        players = retrying_find_elements(driver, By.CSS_SELECTOR, "a[href*='/player/']")
        if not players:
            print(f"No players found for team URL: {team_url}")
            continue

        for player in players:
            try:
                player_name = player.text
                player_url = player.get_attribute('href')
                print(f"Scraping player: {player_name}, URL: {player_url}")

                # Navigate to player page
                driver.get(player_url)
                WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

                # Extract player stats here, using the correct HTML structure
                try:
                    appearances = driver.find_element(By.XPATH, "//span[contains(text(),'Appearances')]/following-sibling::span").text
                    goals = driver.find_element(By.XPATH, "//span[contains(text(),'Goals')]/following-sibling::span").text
                    assists = driver.find_element(By.XPATH, "//span[contains(text(),'Assists')]/following-sibling::span").text
                    print(f"Stats for {player_name}: Appearances: {appearances}, Goals: {goals}, Assists: {assists}")
                except NoSuchElementException as e:
                    print(f"Could not extract stats for {player_name}: {e}")

                driver.back()
                sleep(random.uniform(1, 3))  # Random delay after each player
            except StaleElementReferenceException as e:
                print(f"Stale element reference exception for player: {player.text}, URL: {player.get_attribute('href')}, Error: {e}")
            except Exception as e:
                print(f"Error processing player: {e}")

    # Close the driver after scraping
    driver.quit()

scrape_player_stats()


Page source for team URL: https://www.sofascore.com/team/football/tampines-rovers/3043
<html lang="en" translate="no" style="--primary-default: #7a84ff; --primary-variant: #2c3596; --primary-highlight: rgba(122, 132, 255, 0.25); --primary-hover: hsl(235, 100.0%, 78.9%); --primary-selected: hsl(235, 100.0%, 68.9%); --secondary-default: #46c252; --secondary-variant: #15781f; --secondary-highlight: rgba(70, 194, 82, 0.25); --secondary-hover: hsl(126, 50.4%, 56.8%); --secondary-selected: hsl(126, 50.4%, 46.8%); --neutral-default: #828ba1; --neutral-variant: #bcc2cf; --neutral-highlight: rgba(54, 63, 83, 0.5); --on-color-primary: rgba(255, 255, 255, 0.9); --on-color-secondary: rgba(255, 255, 255, 0.6); --on-color-highlight-nLv1: rgba(255, 255, 255, 0.25); --on-color-highlight-nLv2: rgba(255, 255, 255, 0.1); --on-color-default: #ffffff; --on-color-hover: #ffffff; --on-color-selected: #f2f2f2; --surface-s0: #131a21; --surface-s1: #1c2632; --surface-s2: rgba(14, 17, 21, 0.4); --surface-sp: #2a

In [142]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException, TimeoutException, NoSuchElementException
from bs4 import BeautifulSoup
from time import sleep
import random
import os

# Verify the ChromeDriver path
chrome_driver_path = "D:\\Downloads\\chromedriver-win64\\chromedriver-win64\\chromedriver.exe"
if not os.path.exists(chrome_driver_path):
    raise FileNotFoundError(f"ChromeDriver not found at {chrome_driver_path}")

# Set up the ChromeDriver service
service = Service(executable_path=chrome_driver_path)

# Setting up ChromeDriver with anti-detection measures
options = webdriver.ChromeOptions()
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)

# Initialize the WebDriver with the Service object
try:
    driver = webdriver.Chrome(service=service, options=options)
except Exception as e:
    print(f"Failed to initialize WebDriver: {e}")
    raise

# Adding anti-detection measures
driver.execute_cdp_cmd("Page.addScriptToEvaluateOnNewDocument", {
    "source": "Object.defineProperty(navigator, 'webdriver', {get: () => undefined})"
})

# List of team URLs
team_urls = [
    "https://www.sofascore.com/team/football/tampines-rovers/3043",
    "https://www.sofascore.com/team/football/lion-city-sailors/3041",
    "https://www.sofascore.com/team/football/geylang-international/3044",
    "https://www.sofascore.com/team/football/balestier-khalsa/3039",
    "https://www.sofascore.com/team/football/hougang-united/34083",
    "https://www.sofascore.com/team/football/albirex-niigata/34081",
    "https://www.sofascore.com/team/football/young-lions/34082",
    "https://www.sofascore.com/team/football/tanjong-pagar-united/3038"
]

def scrape_player_stats():
    for team_url in team_urls:
        driver.get(team_url)
        WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))
        sleep(random.uniform(1, 3))  # Random delay to mimic human interaction

        # Use BeautifulSoup to parse the page source
        soup = BeautifulSoup(driver.page_source, 'html.parser')

        # Find player links
        player_links = soup.select("a[href*='/player/']")
        if not player_links:
            print(f"No players found for team URL: {team_url}")
            continue

        for player_link in player_links:
            player_name = player_link.text
            player_url = player_link['href']
            print(f"Scraping player: {player_name}, URL: {player_url}")

            # Navigate to player page
            driver.get(player_url)
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

            # Extract player stats here, using the correct HTML structure
            try:
                appearances = driver.find_element(By.XPATH, "//span[contains(text(),'Appearances')]/following-sibling::span").text
                goals = driver.find_element(By.XPATH, "//span[contains(text(),'Goals')]/following-sibling::span").text
                assists = driver.find_element(By.XPATH, "//span[contains(text(),'Assists')]/following-sibling::span").text
                print(f"Stats for {player_name}: Appearances: {appearances}, Goals: {goals}, Assists: {assists}")
            except NoSuchElementException as e:
                print(f"Could not extract stats for {player_name}: {e}")

            driver.back()
            sleep(random.uniform(1, 3))  # Random delay after each player

    # Close the driver after scraping
    driver.quit()

scrape_player_stats()


No players found for team URL: https://www.sofascore.com/team/football/tampines-rovers/3043
No players found for team URL: https://www.sofascore.com/team/football/lion-city-sailors/3041
No players found for team URL: https://www.sofascore.com/team/football/geylang-international/3044
No players found for team URL: https://www.sofascore.com/team/football/balestier-khalsa/3039
No players found for team URL: https://www.sofascore.com/team/football/hougang-united/34083
No players found for team URL: https://www.sofascore.com/team/football/albirex-niigata/34081
No players found for team URL: https://www.sofascore.com/team/football/young-lions/34082
No players found for team URL: https://www.sofascore.com/team/football/tanjong-pagar-united/3038


In [150]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException
from bs4 import BeautifulSoup
from time import sleep
import random
import os

# Verify the ChromeDriver path
chrome_driver_path = "D:\\Downloads\\chromedriver-win64\\chromedriver-win64\\chromedriver.exe"
if not os.path.exists(chrome_driver_path):
    raise FileNotFoundError(f"ChromeDriver not found at {chrome_driver_path}")

# Set up the ChromeDriver service
service = Service(executable_path=chrome_driver_path)

# Setting up ChromeDriver with anti-detection measures
options = webdriver.ChromeOptions()
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)

# Initialize the WebDriver with the Service object
try:
    driver = webdriver.Chrome(service=service, options=options)
except Exception as e:
    print(f"Failed to initialize WebDriver: {e}")
    raise

# Adding anti-detection measures
driver.execute_cdp_cmd("Page.addScriptToEvaluateOnNewDocument", {
    "source": "Object.defineProperty(navigator, 'webdriver', {get: () => undefined})"
})

# List of team URLs
team_urls = [
    "https://www.sofascore.com/team/football/tampines-rovers/3043",
    "https://www.sofascore.com/team/football/lion-city-sailors/3041",
    "https://www.sofascore.com/team/football/geylang-international/3044",
    "https://www.sofascore.com/team/football/balestier-khalsa/3039",
    "https://www.sofascore.com/team/football/hougang-united/34083",
    "https://www.sofascore.com/team/football/albirex-niigata/34081",
    "https://www.sofascore.com/team/football/young-lions/34082",
    "https://www.sofascore.com/team/football/tanjong-pagar-united/3038"
]

def scrape_player_stats():
    for team_url in team_urls:
        driver.get(team_url)
        WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))
        sleep(random.uniform(1, 3))  # Random delay to mimic human interaction

        # Use BeautifulSoup to parse the page source
        soup = BeautifulSoup(driver.page_source, 'html.parser')

        # Find player links
        player_links = soup.select("a[href*='/player/']")
        if not player_links:
            print(f"No players found for team URL: {team_url}")
            continue

        for player_link in player_links:
            player_name = player_link.text
            player_url = "https://www.sofascore.com" + player_link['href']
            print(f"Scraping player: {player_name}, URL: {player_url}")

            # Navigate to player page
            driver.get(player_url)
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

            # Extract player stats here, using the correct HTML structure
            try:
                appearances = driver.find_element(By.XPATH, "//span[contains(text(),'Appearances')]/following-sibling::span").text
                goals = driver.find_element(By.XPATH, "//span[contains(text(),'Goals')]/following-sibling::span").text
                assists = driver.find_element(By.XPATH, "//span[contains(text(),'Assists')]/following-sibling::span").text
                print(f"Stats for {player_name}: Appearances: {appearances}, Goals: {goals}, Assists: {assists}")
            except NoSuchElementException as e:
                print(f"Could not extract stats for {player_name}: {e}")

            driver.back()
            sleep(random.uniform(1, 3))  # Random delay after each player

    # Close the driver after scraping
    driver.quit()

scrape_player_stats()


No players found for team URL: https://www.sofascore.com/team/football/tampines-rovers/3043
No players found for team URL: https://www.sofascore.com/team/football/lion-city-sailors/3041
No players found for team URL: https://www.sofascore.com/team/football/geylang-international/3044
No players found for team URL: https://www.sofascore.com/team/football/balestier-khalsa/3039
No players found for team URL: https://www.sofascore.com/team/football/hougang-united/34083
No players found for team URL: https://www.sofascore.com/team/football/albirex-niigata/34081
No players found for team URL: https://www.sofascore.com/team/football/young-lions/34082
No players found for team URL: https://www.sofascore.com/team/football/tanjong-pagar-united/3038


### New Scrape

In [38]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException
from time import sleep
import random
import os

# Verify the ChromeDriver path
chrome_driver_path = "D:\\Downloads\\chromedriver-win64\\chromedriver-win64\\chromedriver.exe"
if not os.path.exists(chrome_driver_path):
    raise FileNotFoundError(f"ChromeDriver not found at {chrome_driver_path}")

# Set up the ChromeDriver service
service = Service(executable_path=chrome_driver_path)

# Setting up ChromeDriver with anti-detection measures
options = webdriver.ChromeOptions()
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)

# Initialize the WebDriver with the Service object
try:
    driver = webdriver.Chrome(service=service, options=options)
except Exception as e:
    print(f"Failed to initialize WebDriver: {e}")
    raise

# Adding anti-detection measures
driver.execute_cdp_cmd("Page.addScriptToEvaluateOnNewDocument", {
    "source": "Object.defineProperty(navigator, 'webdriver', {get: () => undefined})"
})

# Sofascore Singapore Premier League URL
base_url = "https://www.sofascore.com/tournament/football/singapore/premier-league/634#id:59708"

def scrape_singaporean_players():
    driver.get(base_url)
    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

    # Fetch the list of teams
    teams = driver.find_elements(By.CSS_SELECTOR, "a[href*='/team/']")
    team_urls = [(team.text, team.get_attribute('href')) for team in teams]

    for team_name, team_url in team_urls:
        print(f"Scraping team: {team_name}")
        driver.get(team_url)
        sleep(random.uniform(1, 3))  # Random delay to mimic human interaction

        # Ensure the view is switched to table view
        try:
            # Find the toggle switch for table view using its unique label
            list_view_toggle = driver.find_element(By.CSS_SELECTOR, "label[for^='listTeamPlayers'] div[role='radio']")
            list_view_toggle.click()
            print(f"Switched to table view for {team_name}")
            sleep(2)  # Allow time for the view to switch
        except NoSuchElementException:
            print("Table view button not found. Assuming already in table view.")
        
        # Locate player rows in the table
        try:
            player_rows = driver.find_elements(By.CSS_SELECTOR, "tr.TableRow")
            if not player_rows:
                print(f"No players found in the table for {team_name}.")
                continue

            for row in player_rows:
                try:
                    player_link_element = row.find_element(By.CSS_SELECTOR, "a[href*='/player/']")
                    player_name = player_link_element.text.strip()
                    player_url = player_link_element.get_attribute('href')
                    full_player_url = f"https://www.sofascore.com{player_url}"  # Build full URL
                    print(f"Found player: {player_name}, URL: {full_player_url}")

                    # Navigate to the player page
                    driver.get(full_player_url)
                    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

                    # Extract all data within <div class="Box klGMtt">
                    try:
                        player_data_box = driver.find_element(By.CSS_SELECTOR, "div.Box.klGMtt")
                        player_data = player_data_box.text  # Extract the text content
                        print(f"Data for {player_name}:\n{player_data}\n")

                    except NoSuchElementException:
                        print(f"Error: Could not find player data for {player_name}.")
                    except Exception as e:
                        print(f"Error extracting data for {player_name}: {e}")

                    driver.back()
                    sleep(random.uniform(1, 3))  # Random delay after each player

                except NoSuchElementException:
                    print(f"Error: Could not find player link in row.")

        except Exception as e:
            print(f"Failed to find players for {team_name}: {e}")

        driver.back()

    # Close the driver after scraping
    driver.quit()

scrape_singaporean_players()


Scraping team: 1
Tampines Rovers
12
+26
30
Table view button not found. Assuming already in table view.
No players found in the table for 1
Tampines Rovers
12
+26
30.
Scraping team: 2
Lion City Sailors
11
+28
28
Table view button not found. Assuming already in table view.
No players found in the table for 2
Lion City Sailors
11
+28
28.
Scraping team: 3
Geylang Int.
12
+20
21
Table view button not found. Assuming already in table view.
No players found in the table for 3
Geylang Int.
12
+20
21.
Scraping team: 4
Balestier Khalsa
11
+2
16
Table view button not found. Assuming already in table view.
No players found in the table for 4
Balestier Khalsa
11
+2
16.
Scraping team: 5
Hougang Utd
12
-12
13
Table view button not found. Assuming already in table view.
No players found in the table for 5
Hougang Utd
12
-12
13.
Scraping team: 6
Albirex Niigata
12
-15
10
Table view button not found. Assuming already in table view.
No players found in the table for 6
Albirex Niigata
12
-15
10.
Scraping

In [ ]:
<div elevation=",3" class="Box cKvany"><div display="none,block" class="Box jZVaGr"><div color="onSurface.nLv1" class="Text jRDMbQ">Players</div><div display="flex" class="Box Flex khxXvq cQgcrM"><label for="boxTeamPlayers-0.719036610582664"><div display="flex" cursor="pointer" class="Box Flex kozMpa jLRkRA"><input id="boxTeamPlayers-0.719036610582664" name="players" type="radio" value="box" checked="" style="display: none;"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper fyGiev"><path d="M12 2c5.52 0 10 4.48 10 10s-4.48 10-10 10S2 17.52 2 12 6.48 2 12 2zm0 2c-4.41 0-8 3.59-8 8s3.59 8 8 8 8-3.59 8-8-3.59-8-8-8zm0 2a6 6 0 1 1 0 12 6 6 0 0 1 0-12z" fill="var(--primary-default)" fill-rule="evenodd"></path></svg><span color="onSurface.nLv1" class="Text fZjCfN">Box View</span></div></label><label for="listTeamPlayers-0.719036610582664"><div display="flex" cursor="pointer" class="Box Flex kozMpa jLRkRA"><input id="listTeamPlayers-0.719036610582664" name="players" type="radio" value="list" style="display: none;"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper fyGiev"><g fill="var(--primary-default)" fill-rule="evenodd"><path fill="primary.default" d="M12 2C6.5 2 2 6.5 2 12s4.5 10 10 10 10-4.5 10-10S17.5 2 12 2zm0 18c-4.4 0-8-3.6-8-8s3.6-8 8-8 8 3.6 8 8-3.6 8-8 8z"></path></g></svg><span color="onSurface.nLv1" class="Text fZjCfN">List view</span></div></label></div><div class="Box fTPNOD"><div class="Box klGMtt"><div class="Box RFLMf"><div class="Box klGMtt"><span color="sofaSingles.live" class="Text WXutH">Forward</span></div></div><div display="flex" wrap="wrap" class="Box Flex kUNxVa kpyaMP"><div class="Box gDjnsl"><a href="/player/boris-kopitovic/843260"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/843260/image" alt="Boris Kopitović" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">9</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Boris Kopitović</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="sofaSingles.live" class="Text WXutH">F</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/me.png" alt="ME" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">MNE</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/kunori-seia/1218518"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/1218518/image" alt="Seia Kunori" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">7</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Seia Kunori</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="sofaSingles.live" class="Text WXutH">F</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/jp.png" alt="JP" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">JPN</span></div></div></div></a></div></div></div><div class="Box klGMtt"><div class="Box RFLMf"><div class="Box klGMtt"><span color="secondary.default" class="Text FiyPX">Midfielder</span></div></div><div display="flex" wrap="wrap" class="Box Flex kUNxVa kpyaMP"><div class="Box gDjnsl"><a href="/player/faris-ramli/851803"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/851803/image" alt="Faris Ramli" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">30</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Faris Ramli</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/kyoga-nakamura/358968"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/358968/image" alt="Kyoga Nakamura" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">10</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Kyoga Nakamura</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/jp.png" alt="JP" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">JPN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/shah-shahiran/929540"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/929540/image" alt="Shah Shahiran" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">8</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Shah Shahiran</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/taufik-suparno/851810"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/851810/image" alt="Taufik Suparno" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">13</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Taufik Suparno</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/joel-chew-joon-herng/979261"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/979261/image" alt="Joel Chew Joon Herng" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">12</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Joel Chew Joon Herng</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/yasir-hanapi/812590"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/812590/image" alt="Yasir Hanapi" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">18</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Yasir Hanapi</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/jared-gallagher/1184545"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/1184545/image" alt="Jared Gallagher" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">6</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Jared Gallagher</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/saifullah-akbar/835102"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/835102/image" alt="Saifullah Akbar" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">20</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Saifullah Akbar</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/caelan-cheong-tze-jay/1401682"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/1401682/image" alt="Caelan Cheong" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">58</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Caelan Cheong</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/kieran-tan/1860320"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="/static/images/placeholders/player.svg" alt="Kieran Tan" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">80</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Kieran Tan</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="secondary.default" class="Text FiyPX">M</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div></div></div><div class="Box klGMtt"><div class="Box RFLMf"><div class="Box klGMtt"><span color="primary.default" class="Text fJEWkR">Defender</span></div></div><div display="flex" wrap="wrap" class="Box Flex kUNxVa kpyaMP"><div class="Box gDjnsl"><a href="/player/shuya-yamashita/1108290"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/1108290/image" alt="Shuya Yamashita" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">4</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Shuya Yamashita</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="primary.default" class="Text fJEWkR">D</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/jp.png" alt="JP" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">JPN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/glenn-kweh/1116213"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/1116213/image" alt="Glenn Kweh" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">11</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Glenn Kweh</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="primary.default" class="Text fJEWkR">D</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/milos-zlatkovic/795891"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/795891/image" alt="Miloš Zlatković" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">33</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Miloš Zlatković</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="primary.default" class="Text fJEWkR">D</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/rs.png" alt="RS" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SRB</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/irfan-najeeb/922337"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/922337/image" alt="Irfan Najeeb" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">23</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Irfan Najeeb</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="primary.default" class="Text fJEWkR">D</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/amirul-adli-bin-azmi/851807"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/851807/image" alt="Amirul Adli Bin Azmi" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">5</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Amirul Adli Bin Azmi</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="primary.default" class="Text fJEWkR">D</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/amirul-haikal-hassim/1086348"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/1086348/image" alt="Amirul Haikal Hassim" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">17</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Amirul Haikal Hassim</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="primary.default" class="Text fJEWkR">D</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/syahrul-sazali/1014758"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/1014758/image" alt="Syahrul Sazali" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">22</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Syahrul Sazali</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="primary.default" class="Text fJEWkR">D</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div></div></div><div class="Box klGMtt"><div class="Box RFLMf"><div class="Box klGMtt"><span color="sofaSingles.value" class="Text vEssy">Goalkeeper</span></div></div><div display="flex" wrap="wrap" class="Box Flex kUNxVa kpyaMP"><div class="Box gDjnsl"><a href="/player/syazwan-buhari/922347"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/922347/image" alt="Syazwan Buhari" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">24</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Syazwan Buhari</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="sofaSingles.value" class="Text vEssy">G</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div><div class="Box gDjnsl"><a href="/player/ridhuan-barudin/1019434"><div display="flex" direction="column" cursor="pointer" class="Box Flex kUbuld jRvcdE"><div class="Box gxLneH"><img src="https://api.sofascore.app/api/v1/player/1019434/image" alt="Ridhuan Barudin" width="64" height="64" class="Img bFoDOL"><div class="Box ghTCXM"><div color="surface.s1" class="Text jmvTmM">31</div></div></div><div display="flex" class="Box Flex kJrred kFvGEE"><div color="onSurface.nLv1" class="Text cOreSJ">Ridhuan Barudin</div></div><div display="flex" class="Box Flex hWEWeE MHPeY"><span color="sofaSingles.value" class="Text vEssy">G</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv1" class="Text dJOWjw">SIN</span></div></div></div></a></div></div></div></div></div><div display="block,none" class="Box gsCIwz"><div class="Box klGMtt"><a href="/manager/gavin-lee/794410"><div display="flex" class="Box Flex jHdcMt jLRkRA"><div class="Box bWPCIp"><img src="https://api.sofascore.app/api/v1/manager/794410/image" width="56" height="56" class="Img hpocRq" style="width: 100%; height: 100%;"></div><div class="Box hwjEH"><div color="onSurface.nLv1" class="Text hLrEqo">Gavin Lee</div><div display="flex" class="Box Flex ggRYVx WzAFW"><div color="onSurface.nLv3" class="Text eMhAJJ">Coach</div><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div></div></a><div class="Box dflyPx"><div display="flex" class="Box Flex jilvhL jLRkRA"><div class="Box fgrzny"></div><div class="Box klGMtt"><span color="sofaSingles.live" class="Text WXutH">Forward</span></div></div><a href="/player/boris-kopitovic/843260"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/843260/image" alt="Boris Kopitović" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Boris Kopitović</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">9</span><span color="onSurface.nLv3" class="Text eMhAJJ">29 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/me.png" alt="ME" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">MNE</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/kunori-seia/1218518"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/1218518/image" alt="Seia Kunori" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex hguFSO hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Seia Kunori</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">7</span><span color="onSurface.nLv3" class="Text eMhAJJ">23 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/jp.png" alt="JP" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">JPN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a></div><div class="Box dflyPx"><div display="flex" class="Box Flex jilvhL jLRkRA"><div class="Box jDeERy"></div><div class="Box klGMtt"><span color="secondary.default" class="Text FiyPX">Midfielder</span></div></div><a href="/player/faris-ramli/851803"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/851803/image" alt="Faris Ramli" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Faris Ramli</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">30</span><span color="onSurface.nLv3" class="Text eMhAJJ">31 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/kyoga-nakamura/358968"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/358968/image" alt="Kyoga Nakamura" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Kyoga Nakamura</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">10</span><span color="onSurface.nLv3" class="Text eMhAJJ">28 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/jp.png" alt="JP" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">JPN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/shah-shahiran/929540"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/929540/image" alt="Shah Shahiran" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Shah Shahiran</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">8</span><span color="onSurface.nLv3" class="Text eMhAJJ">24 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/taufik-suparno/851810"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/851810/image" alt="Taufik Suparno" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Taufik Suparno</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">13</span><span color="onSurface.nLv3" class="Text eMhAJJ">28 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/joel-chew-joon-herng/979261"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/979261/image" alt="Joel Chew Joon Herng" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Joel Chew Joon Herng</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">12</span><span color="onSurface.nLv3" class="Text eMhAJJ">24 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/yasir-hanapi/812590"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/812590/image" alt="Yasir Hanapi" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Yasir Hanapi</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">18</span><span color="onSurface.nLv3" class="Text eMhAJJ">35 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/jared-gallagher/1184545"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/1184545/image" alt="Jared Gallagher" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Jared Gallagher</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">6</span><span color="onSurface.nLv3" class="Text eMhAJJ">22 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/saifullah-akbar/835102"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/835102/image" alt="Saifullah Akbar" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Saifullah Akbar</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">20</span><span color="onSurface.nLv3" class="Text eMhAJJ">25 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/caelan-cheong-tze-jay/1401682"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/1401682/image" alt="Caelan Cheong" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Caelan Cheong</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">58</span><span color="onSurface.nLv3" class="Text eMhAJJ">18 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/kieran-tan/1860320"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="/static/images/placeholders/player.svg" alt="Kieran Tan" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex hguFSO hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Kieran Tan</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">80</span><span color="onSurface.nLv3" class="Text eMhAJJ">16 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a></div><div class="Box dflyPx"><div display="flex" class="Box Flex jilvhL jLRkRA"><div class="Box iiuZQk"></div><div class="Box klGMtt"><span color="primary.default" class="Text fJEWkR">Defender</span></div></div><a href="/player/shuya-yamashita/1108290"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/1108290/image" alt="Shuya Yamashita" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Shuya Yamashita</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">4</span><span color="onSurface.nLv3" class="Text eMhAJJ">25 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/jp.png" alt="JP" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">JPN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/glenn-kweh/1116213"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/1116213/image" alt="Glenn Kweh" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Glenn Kweh</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">11</span><span color="onSurface.nLv3" class="Text eMhAJJ">24 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/milos-zlatkovic/795891"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/795891/image" alt="Miloš Zlatković" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Miloš Zlatković</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">33</span><span color="onSurface.nLv3" class="Text eMhAJJ">27 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/rs.png" alt="RS" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SRB</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/irfan-najeeb/922337"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/922337/image" alt="Irfan Najeeb" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Irfan Najeeb</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">23</span><span color="onSurface.nLv3" class="Text eMhAJJ">25 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/amirul-adli-bin-azmi/851807"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/851807/image" alt="Amirul Adli Bin Azmi" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Amirul Adli Bin Azmi</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">5</span><span color="onSurface.nLv3" class="Text eMhAJJ">28 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/amirul-haikal-hassim/1086348"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/1086348/image" alt="Amirul Haikal Hassim" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Amirul Haikal Hassim</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">17</span><span color="onSurface.nLv3" class="Text eMhAJJ">24 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/syahrul-sazali/1014758"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/1014758/image" alt="Syahrul Sazali" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex hguFSO hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Syahrul Sazali</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">22</span><span color="onSurface.nLv3" class="Text eMhAJJ">26 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a></div><div class="Box dflyPx"><div display="flex" class="Box Flex jilvhL jLRkRA"><div class="Box jUIgdv"></div><div class="Box klGMtt"><span color="sofaSingles.value" class="Text vEssy">Goalkeeper</span></div></div><a href="/player/syazwan-buhari/922347"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/922347/image" alt="Syazwan Buhari" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex dksRWk hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Syazwan Buhari</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">24</span><span color="onSurface.nLv3" class="Text eMhAJJ">31 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a><a href="/player/ridhuan-barudin/1019434"><div display="flex" cursor="pointer" class="Box Flex jBQtbp jLRkRA"><img src="https://api.sofascore.app/api/v1/player/1019434/image" alt="Ridhuan Barudin" width="40" height="40" class="Img cNprQ"><div display="flex" direction="row" class="Box Flex hguFSO hLKouD"><div display="flex" direction="column" class="Box Flex ggRYVx dMUPzG"><div color="onSurface.nLv1" class="Text ietnEf">Ridhuan Barudin</div><div display="flex" class="Box Flex ggRYVx WzAFW"><span color="onSurface.nLv3" class="Text eMhAJJ">31</span><span color="onSurface.nLv3" class="Text eMhAJJ">37 yrs</span><div display="flex" class="Box Flex ggRYVx jLRkRA"><img src="/static/images/flags/sg.png" alt="SG" width="16" height="16" class="Img hpocRq"><span color="onSurface.nLv3" class="Text bcLgJU">SIN</span></div></div></div><button class="Button gzbfWJ"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper idaRdE"><path fill="var(--primary-default)" d="M17 14V6l-2-2h-2V2h-2v2H9L7 6v8l-2 2v2h14v-2l-2-2zm-9.17 2 .59-.59.59-.59V6.83L9.84 6h4.34l.83.83v8l.59.59.59.59H7.83V16zM14 20h-4v2h4v-2z" fill-rule="evenodd" m="0"></path></svg></button></div></div></a></div></div></div></div>

In [ ]:
<div display="flex" class="Box Flex khxXvq cQgcrM"><label for="boxTeamPlayers-0.719036610582664"><div display="flex" cursor="pointer" class="Box Flex kozMpa jLRkRA"><input id="boxTeamPlayers-0.719036610582664" name="players" type="radio" value="box" checked="" style="display: none;"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper fyGiev"><g fill="var(--primary-default)" fill-rule="evenodd"><path fill="primary.default" d="M12 2C6.5 2 2 6.5 2 12s4.5 10 10 10 10-4.5 10-10S17.5 2 12 2zm0 18c-4.4 0-8-3.6-8-8s3.6-8 8-8 8 3.6 8 8-3.6 8-8 8z"></path></g></svg><span color="onSurface.nLv1" class="Text fZjCfN">Box View</span></div></label><label for="listTeamPlayers-0.719036610582664"><div display="flex" cursor="pointer" class="Box Flex kozMpa jLRkRA"><input id="listTeamPlayers-0.719036610582664" name="players" type="radio" value="list" style="display: none;"><svg width="24" height="24" viewBox="0 0 24 24" fill="var(--primary-default)" class="SvgWrapper fyGiev"><path d="M12 2c5.52 0 10 4.48 10 10s-4.48 10-10 10S2 17.52 2 12 6.48 2 12 2zm0 2c-4.41 0-8 3.59-8 8s3.59 8 8 8 8-3.59 8-8-3.59-8-8-8zm0 2a6 6 0 1 1 0 12 6 6 0 0 1 0-12z" fill="var(--primary-default)" fill-rule="evenodd"></path></svg><span color="onSurface.nLv1" class="Text fZjCfN">List view</span></div></label></div>

### Gemini

In [71]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.exceptions import NoSuchElementException, StaleElementReferenceException
from time import sleep
import random
import os

# Verify the ChromeDriver path
chrome_driver_path = "D:\\Downloads\\chromedriver-win64\\chromedriver-win64\\chromedriver.exe"
if not os.path.exists(chrome_driver_path):
    raise FileNotFoundError(f"ChromeDriver not found at {chrome_driver_path}")

# Set up the ChromeDriver service
service = Service(executable_path=chrome_driver_path)

# Setting up ChromeDriver with anti-detection measures
options = webdriver.ChromeOptions()
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)

# Initialize the WebDriver with the Service object
try:
    driver = webdriver.Chrome(service=service, options=options)
except Exception as e:
    print(f"Failed to initialize WebDriver: {e}")
    raise

# Adding anti-detection measures
driver.execute_cdp_cmd("Page.addScriptToEvaluateOnNewDocument", {
    "source": "Object.defineProperty(navigator, 'webdriver', {get: () => undefined})"
})

# Sofascore Singapore Premier League URL
base_url = "https://www.sofascore.com/tournament/football/singapore/premier-league/634#id:59708"


def scrape_singaporean_players(max_retries=3):
    """
    Scrapes Singaporean players from Sofascore with retries for potential exceptions.

    Args:
        max_retries (int, optional): The maximum number of retries for failed element lookups. Defaults to 3.
    """
    driver.get(base_url)
    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

    # Navigate to each team page
    teams = driver.find_elements(By.CSS_SELECTOR, "a[href*='/team/']")
    for team in teams:
        team_name = team.text
        team_url = team.get_attribute('href')
        print(f"Scraping team: {team_name}")

        driver.get(team_url)
        sleep(random.uniform(1, 3))  # Random delay to mimic human interaction

        try:
            players = driver.find_elements(By.CSS_SELECTOR, "a[href*='/player/']")
        except (NoSuchElementException, StaleElementReferenceException) as e:
            # Retry finding players if element lookup fails (up to max_retries)
            print(f"Error finding players on team page: {e}")
            if max_retries > 0:
                scrape_singaporean_players(max_retries - 1)
                continue
            else:
                print(f"Failed to find players after {max_retries} retries. Skipping team.")
                continue

        for player in players:
            player_name = player.text
            player_url = player.get_attribute('href')

            # Navigate to player page
            driver.get(player_url)
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

            # Example: check for Singapore nationality (update selector as necessary)
            try:
                nationality = driver.find_element(By.XPATH, "//div[contains(text(),'Singapore')]")
                if nationality:
                    print(f"Singaporean player found: {player_name}, URL: {player_url}")

                    # Extract player stats here, using the correct HTML structure
                    # Example:
                    # appearances_element = driver.find_element(By.XPATH, "//span[text()='Appearances']/following-sibling::span")
                    # appearances = appearances_element.text
                    #
                    # goals_element = driver.find_element(By.XPATH, "//span[text()='Goals']/following-sibling::span")
                    # goals = goals_element.text
                    #
                    # # Add more stats as needed

                    # Save or process the data as needed
                    # Example:
                    # player_data = {
                    #     'name': player_name,
                    #     'url': player_url,
                    #     'appearances': appearances,
                    #     'goals': goals,
                    #     # Add more stats
                    # }
                    #
                    # # Append player data to a list or save to a file
                    # player_data_list.append(player_data)

            except (NoSuchElementException, StaleElementReferenceException) as e:
                print(f"Player {player_name} does not match criteria or an error occurred: {e}")

            driver.back()
            sleep(random.uniform(1, 3))

scrape_singaporean_players()

ModuleNotFoundError: No module named 'selenium.webdriver.common.exceptions'

In [73]:
import sys

print(sys.executable)

D:\Anaconda\python.exe


In [81]:
import subprocess

try:
    subprocess.check_call(['pip', 'list'])
    print("Selenium is installed.")
except subprocess.CalledProcessError:
    print("Selenium is not installed.")

Selenium is installed.


In [152]:
import requests

from bs4 import BeautifulSoup

In [154]:
response = requests.get(
    'https://www.sofascore.com/team/football/tampines-rovers/3043',
    headers={'User-Agent': 'Mozilla/5.0'} # you'll be blocked if you don't use some type of user agent
)

In [156]:
soup = BeautifulSoup(response.text, 'html.parser')

In [158]:
# These are the headers we need to access the API
headers = {
    'authority': 'api.sofascore.com',
    'accept': '*/*',
    'accept-language': 'en-US,en;q=0.9',
    'cache-control': 'max-age=0',
    'dnt': '1',
    'if-none-match': 'W/"4bebed6144"',
    'origin': 'https://www.sofascore.com',
    'referer': 'https://www.sofascore.com/',
    'sec-ch-ua': '"Not.A/Brand";v="8", "Chromium";v="114"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-platform': '"macOS"',
    'sec-fetch-dest': 'empty',
    'sec-fetch-mode': 'cors',
    'sec-fetch-site': 'same-site',
    'user-agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36',
}

# you'll need to change the url to match the one you copied. As you can see they have some sort of match id to identify the game --> 10385636
response = requests.get('https://api.sofascore.com/api/v1/team/3043', headers=headers)

In [160]:
response

<Response [200]>

In [162]:
shots = response.json()

In [164]:
shots

{'team': {'name': 'Tampines Rovers',
  'slug': 'tampines-rovers',
  'shortName': 'Tampines Rovers',
  'gender': 'M',
  'sport': {'name': 'Football', 'slug': 'football', 'id': 1},
  'category': {'name': 'Singapore',
   'slug': 'singapore',
   'sport': {'name': 'Football', 'slug': 'football', 'id': 1},
   'id': 45,
   'country': {'alpha2': 'SG', 'alpha3': 'SGP', 'name': 'Singapore'},
   'flag': 'singapore',
   'alpha2': 'SG'},
  'tournament': {'name': 'Premier League',
   'slug': 'premier-league',
   'category': {'name': 'Singapore',
    'slug': 'singapore',
    'sport': {'name': 'Football', 'slug': 'football', 'id': 1},
    'id': 45,
    'country': {'alpha2': 'SG', 'alpha3': 'SGP', 'name': 'Singapore'},
    'flag': 'singapore',
    'alpha2': 'SG'},
   'uniqueTournament': {'name': 'Singapore Premier League',
    'slug': 'premier-league',
    'primaryColorHex': '#532657',
    'secondaryColorHex': '#db2234',
    'category': {'name': 'Singapore',
     'slug': 'singapore',
     'sport': {'na

In [166]:
import requests

# Define the headers for the API request
headers = {
    'authority': 'api.sofascore.com',
    'accept': '*/*',
    'accept-language': 'en-US,en;q=0.9',
    'cache-control': 'max-age=0',
    'dnt': '1',
    'if-none-match': 'W/"4bebed6144"',
    'origin': 'https://www.sofascore.com',
    'referer': 'https://www.sofascore.com/',
    'sec-ch-ua': '"Not.A/Brand";v="8", "Chromium";v="114"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-platform': '"macOS"',
    'sec-fetch-dest': 'empty',
    'sec-fetch-mode': 'cors',
    'sec-fetch-site': 'same-site',
    'user-agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36',
}

# Make a request to the team endpoint to get team data
team_response = requests.get('https://api.sofascore.com/api/v1/team/3043', headers=headers)
team_data = team_response.json()

# Extract the player IDs from the team data
player_ids = [player['id'] for player in team_data['players']]

# Fetch detailed information for each player
players_info = []
for player_id in player_ids:
    player_response = requests.get(f'https://api.sofascore.com/api/v1/player/{player_id}', headers=headers)
    players_info.append(player_response.json())

# Print player information
for player in players_info:
    print(player)


KeyError: 'players'

In [170]:

import json

from selenium import webdriver # selenium 4.20.0
from selenium.webdriver.chrome.service import Service as ChromeService

from webdriver_manager.chrome import ChromeDriverManager # version 4.0.1
options = webdriver.ChromeOptions()
options.set_capability(
    "goog:loggingPrefs", {"performance": "ALL", "browser": "ALL"}
)

# Make sure you already have Chrome installed
driver = webdriver.Chrome(service=ChromeService(ChromeDriverManager().install()), options=options)
driver.set_page_load_timeout(10)

try:
    driver.get("https://www.sofascore.com/inter-miami-cf-new-york-red-bulls/gabsccKc#id:11911622,tab:statistics")
except:
    pass


driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
# extract requests from logs
logs_raw = driver.get_log("performance")
logs = [json.loads(lr["message"])["message"] for lr in logs_raw]
for x in logs:
    if 'shotmap' in x['params'].get('headers', {}).get(':path', ''):
        print(x['params'].get('headers', {}).get(':path'))
        break

test = json.loads(driver.execute_cdp_cmd('Network.getResponseBody', {'requestId': x["params"]["requestId"]})['body'])['shotmap']
test[0]
 

KeyError: 'shotmap'